In [1]:
import pandas as pd
import scipy.io
import numpy as np
from numpy.lib.stride_tricks import sliding_window_view
from pywt import wavedec
from scipy.signal import welch
import os
import warnings

# Suppress warnings
warnings.filterwarnings('ignore')


# Define functions for normalization and feature extraction (as in your provided code)
def normalize(emg):
    mean = np.mean(emg, axis=0).reshape(1, 12)  # Shape: (1, 12) for 12 channels
    std = np.std(emg, axis=0).reshape(1, 12)    # Shape: (1, 12) for 12 channels
    std[std == 0]=1e-10
    return (emg - mean) / std

def zero_crossings(data):
    data = data - data.mean()
    return ((data[:-1] * data[1:]) < 0).sum()

def waveform_length(array):
    return np.sum(np.abs(np.diff(array, n=1, axis=0)))

def wavelets(data):
    writeable_data = np.copy(data.T)
    cA3, cD3, cD2, cD1 = wavedec(writeable_data, 'db7', level=3)
    return [np.abs(cD1).sum(), np.abs(cD2).sum(), np.abs(cD3).sum()]

def hist(data):
    histogram, _ = np.histogram(data, bins=10)
    return histogram

def mav(data):
    return [np.mean(np.abs(data))]

def mean_freq(data, fs=2000):
    f, Pxx = welch(data, fs=fs, nperseg=400)
    return np.sum(f * Pxx) / np.sum(Pxx)

def pwr_spec(data, fs=2000):
    _, Pxx = welch(data, fs=fs, nperseg=400)
    return np.sum(Pxx)

def median_freq(data, fs=2000):
    f, Pxx = welch(data, fs=fs, nperseg=400)
    cumulative_power = np.cumsum(Pxx)
    total_power = cumulative_power[-1]
    median_idx = np.where(cumulative_power >= total_power / 2)[0][0]
    return f[median_idx]

def feature_extract(emg, stimulus, repetition):
    if stimulus.size == 0 or repetition.size == 0 or emg.size == 0 or emg.shape[1] != 12:
        return pd.DataFrame()

    df = pd.DataFrame()

    df['Forearm_Percentage'] = [forearm_percentage.get(patient_id, 0)]
    df['Years_Since_Amputation'] = [years_amputated.get(patient_id, 0)]
    df['Myoelectric_Use'] = [myoelectric_use.get(patient_id, 0)]
    
    values, counts = np.unique(stimulus, return_counts=True)
    df['Stimulus'] = [values[counts.argmax()]]
    values, counts = np.unique(repetition, return_counts=True)
    df['Repetition'] = [values[counts.argmax()]]

    for i in range(12):
        channel_data = emg[:, i]
        df[f'Var{i+1}'] = [channel_data.var()]
        df[f'zc{i+1}'] = [zero_crossings(channel_data)]
        df[f'wl{i+1}'] = [waveform_length(channel_data)]
        histogram = hist(channel_data)
        for j in range(len(histogram)):
            df[f'hist{i+1}_{j}'] = [histogram[j]]
        dwt = wavelets(channel_data)
        for k in range(len(dwt)):
            df[f'dwt{i+1}_{k}'] = [dwt[k]]
        df[f'mav{i+1}_0'] = mav(channel_data)[0]
        df[f'mnf{i+1}'] = [mean_freq(channel_data)]
        df[f'ps{i+1}'] = [pwr_spec(channel_data)]
        df[f'mdf{i+1}'] = [median_freq(channel_data)]

    return df

# Path to the data folder
base_path = 'data/DB3_s{}/S{}_E1_A1.mat'

# Create a folder for output
output_folder = '/Users/aidantang/Desktop/Gesture_recog/Feature_extract_dataV2'
os.makedirs(output_folder, exist_ok=True)



In [2]:
# Loop through each patient
for patient_id in range(1, 12):
    file_path = base_path.format(patient_id, patient_id)
    if not os.path.exists(file_path):
        print(f"File not found for patient {patient_id}: {file_path}")
        continue

    print(f"Processing patient {patient_id}")
    mat = scipy.io.loadmat(file_path, matlab_compatible=True)

    # Normalize EMG data
    emg = mat['emg']
    emg_normalized = normalize(emg)
    print(emg.shape)

    # Sliding window segmentation for EMG
    emg_slice = sliding_window_view(emg_normalized, (400, 12))[::200, :]
    emg_slice = emg_slice.reshape((emg_slice.shape[0], emg_slice.shape[2], emg_slice.shape[3]))

    # Sliding window segmentation for stimulus
    stimulus = mat['restimulus']
    stimulus_slice = sliding_window_view(stimulus, (400, 1))[::200, :]
    stimulus_slice = stimulus_slice.reshape((stimulus_slice.shape[0], stimulus_slice.shape[2]))

    forearm_percentage = {
        1: 0.5, 
        2: 0.7,
        3: 0.3,
        4: 0.4,
        5: 0.9,
        6: 0.4,
        7: 0,
        8: 0.5,
        9: 0.9,
        10: 0.5,
        11: 0.9,
    }
    years_amputated = {
        1: 13, 
        2: 6,
        3: 5,
        4: 1,
        5: 1,
        6: 13,
        7: 7,
        8: 5,
        9: 14,
        10: 2,
        11: 5,
    }
    myoelectric_use = {
        1: 13, 
        2: 0,
        3: 8,
        4: 0,
        5: 0,
        6: 0,
        7: 6,
        8: 4,
        9: 14,
        10: 0,
        11: 5,
    }

    ##Define stimulus group mapping
    stimulus_mapping = {
        1: '1',  # Thumb up – grouped with flexor-dominant finger gestures
        2: '1',  # V-sign – flexor-dominant (co-activated fingers, mostly flexors)
        3: '2',  # “German three” – extensor-dominant finger gesture
        4: '2',  # Thumb to little finger – extensor-dominant (four fingers extended)
        5: '2',  # Open hand (finger abduction) – pure extensor group
        6: '1',  # Fist (closed hand) – pure flexor group
        7: '1',  # Pointing index – flexor-dominant (index ext., others flexed)
        8: '2',  # Fingers together extended – pure extensor group
        9: '3',  # Wrist supination (mid-axis) – supination group
        10: '4', # Wrist pronation (mid-axis) – pronation group
        11: '3', # Wrist supination (little-finger axis) – supination group
        12: '4', # Wrist pronation (little-finger axis) – pronation group
        13: '5', # Wrist flexion – wrist flexor group
        14: '6', # Wrist extension (open hand) – wrist extensor group
        15: '7', # Wrist radial deviation – wrist deviation (co-contraction) group
        16: '7', # Wrist ulnar deviation – wrist deviation (co-contraction) group
        17: '6', # Wrist extension (with closed hand) – wrist extensor group
        0:  '0', # Rest
    }

    
    #uncomment below
    stimulus_grouped = np.vectorize(stimulus_mapping.get)(stimulus_slice)

    # Sliding window segmentation for repetition
    repetition = mat['rerepetition']
    repetition_slice = sliding_window_view(repetition, (400, 1))[::200, :]
    repetition_slice = repetition_slice.reshape((repetition_slice.shape[0], repetition_slice.shape[2]))

    # Feature extraction
    patient_features = pd.DataFrame()
    for i in range(emg_slice.shape[0]):
        print(f"Processing stimulus window {i + 1}/{emg_slice.shape} for patient {patient_id}/12")
        #select if use grouped or not (remember to edit output file name)
        features = feature_extract(emg_slice[i, :, :], stimulus_grouped[i, :], repetition_slice[i, :])
        #features = feature_extract(emg_slice[i, :, :], stimulus_slice[i, :], repetition_slice[i, :])
        patient_features = pd.concat([patient_features, features], axis=0)

    # Save each patient's features to a separate CSV
    print(patient_features.shape)
    patient_file = os.path.join(output_folder, f'S{patient_id}_features_regrouped.csv')
    patient_features.to_csv(patient_file, index=False)
    print(f"Features for patient {patient_id} saved to {patient_file}")

print("Feature extraction completed for all patients.")


Processing patient 1
(1825008, 12)
Processing stimulus window 1/(9124, 400, 12) for patient 1/12
Processing stimulus window 2/(9124, 400, 12) for patient 1/12
Processing stimulus window 3/(9124, 400, 12) for patient 1/12
Processing stimulus window 4/(9124, 400, 12) for patient 1/12
Processing stimulus window 5/(9124, 400, 12) for patient 1/12
Processing stimulus window 6/(9124, 400, 12) for patient 1/12
Processing stimulus window 7/(9124, 400, 12) for patient 1/12
Processing stimulus window 8/(9124, 400, 12) for patient 1/12
Processing stimulus window 9/(9124, 400, 12) for patient 1/12
Processing stimulus window 10/(9124, 400, 12) for patient 1/12
Processing stimulus window 11/(9124, 400, 12) for patient 1/12
Processing stimulus window 12/(9124, 400, 12) for patient 1/12
Processing stimulus window 13/(9124, 400, 12) for patient 1/12
Processing stimulus window 14/(9124, 400, 12) for patient 1/12
Processing stimulus window 15/(9124, 400, 12) for patient 1/12
Processing stimulus window 16